In [1]:
import requests
from bs4 import BeautifulSoup
import re , json
import time
from tqdm import tqdm
import pandas as pd

In [2]:
# Creating dictionary to scraped selected attributes
ds_name='scraped_data.csv'
def reset_csv_dataset():
    dict_data = {'state': [],
                 'type': [],
                 'max_price': [],
                 'min_price': [],
                 'address': [],
                 'lat': [],
                 'lng': [],
                 'landArea': [],
                 'builtUp': [],
                 'sizeUnit': [],
                 'level1': [],
                 'level2': [],
                 'level3': []}
    df = pd.DataFrame.from_dict(dict_data)
    df.to_csv(ds_name, index_label=False)

# reset_csv_dataset()
# df2=pd.read_csv('scraped_data.csv')
# print(df2)

def searchValue(data, varName, str_regex, bln_print_Error=False, bln_isNumber=False):
    import re
    try:
        if bln_isNumber:
            res = re.search(str_regex, str(data)).group(1).replace(',','').strip()
        else:
            res = re.search(str_regex, str(data)).group(1).strip()
    except AttributeError:
        res = ''
        if bln_print_Error: print(f'{varName}: (Error: There is no attribute.)')

    return res

In [3]:
# Specify state to scrape
lst_state=['johor']#, 'kuala-lumpur']

# Only choose residential sales
lst_place_type=['all-residential'] #, 'all-commercial', 'all-industrial', 'all-agricultural']
lst_type=['sale']

# Selected attributes to be used in mapping 
attr = ["prices", "address", "attributes", "multilanguagePlace"]

# Specify maxiumum page to scrape
max_page = 100
ds_name='scraped_data.csv'

headers = """
authority: www.iproperty.com.my
method: GET
path: /
scheme: https
accept: text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.9
accept-encoding: gzip, deflate, br
accept-language: en-US,en;q=0.9,fa;q=0.8,de;q=0.7
cache-control: max-age=0
cookie: feature-RWD-6307=true; feature-RWD-6862-1=control; feature-RWD-7170-1=true; feature-RWD-7145-1=true; feature-RWD-7252=control; feature-RWCP-24-1=true; feature-RWD-7274-1=true; feature-RWD-7197=control; feature-RWD-7571=control; _gcl_au=1.1.868914632.1614006197; _ga=GA1.3.670177510.1614006197; _fbp=fb.2.1614006198232.1085373626; _hjTLDTest=1; _hjid=05f07f56-4413-4583-bd03-a0cd6d13505e; __gads=ID=e012a425ddde61d5:T=1614006202:S=ALNI_MY1MNZ3hVX_uRrGNgsJigg9KnLgIw; scarab.visitor=%2228985172CA480CF7%22; ASP.NET_SessionId=hr1o2fly2veh505egdv5t5rx; anonymoususerid=5850c23b-600b-4ebc-9522-7fbf23959a0b; scarab.profile=%225903%7C1614012352%22; scarab.mayAdd=%5B%7B%22i%22%3A%225903%22%7D%2C%7B%22i%22%3A%22101584625%22%7D%5D; KP_UID=ec1361ad-fadb-ee62-3314-88f020b1dcd2; _gid=GA1.3.1896028716.1614154337; _vwo_uuid_v2=DFC6A03DF5B1902DD79575D3D53C0678B|705d37525459f9f466b5d25e700e9aa8; __utmc=108855130; adsblock=yes; _knxcm_=googleT1614165346.0004T1614165346.0005T1614165346.0006T1614165346.0008T1614165346.0010T1614165346.0011T1614165346.0013T1614165346.0015T1614165346.0016T1614165346.0011T1614165346; cloudfront_viewer_country=GB; _hjIncludedInPageviewSample=1; _hjIncludedInSessionSample=1; __utma=108855130.670177510.1614006197.1614165343.1614171002.2; __utmz=108855130.1614171002.2.2.utmcsr=google|utmccn=(organic)|utmcmd=organic|utmctr=(not%20provided); gdpr_notification=yes; _dc_gtm_UA-85157164-4=1; _gat_UA-85157164-4=1; KP_UIDz=bCpm0h5msVzQ7kaqjtRMjQ%3D%3D%3A%3AJU1Q05CSfG6%2FRUhS3Ci8t%2BF6WcvATd7IKkYJGxhJ5dxmZnyRiYIv0CECGWCkMnTz77g2K%2FLcq%2FOFt80CMVM9lzkdXh7iCoRydtmNXg9B6ruLhFrSqXe4iq%2Bre81FeRTckMxpvHrTswP%2FRbKKE5JkWBcahjRdcxBC%2FS4ZaIFN2oZh%2FUhSUsNjXfS1erO1NzoXzne6thIvucSHg1nDJ%2F5TjtDItyb6mswXms3kpe4rI4wtEJNl42tr1S4SmFo2OAlGcX0GrelcZMaSDTK1VSl9cpPK66zvfKN0t6BLFACOUjfFTl7mrmq0YhsF2VH8Pd6uc0PRLhz%2BkvQENIOrEG1Zt1fWupx7kEzE1INpeXJAkzdlkuUNnFMnFQ2orC1gIwG0dfv1a1vuxW6ClPjBVl310RcsT6sC%2BVaZ1EMVwP7z%2F5vjCzJw%2FgNmyw%2Fk4Wc%2FNXsfdce%2FAd%2BarQ03GqmExhOuOjUcHMA4Dn3qt6sWm1uA2bEDxIaZNeARKwcY1EtuZQj1%2B%2B5O8NQnQJFL1GLbPN7ZcpYxUge60IPZKz60KgvkktiiYvQRus2j1cO1OnzV5qo3
sec-fetch-dest: document
sec-fetch-mode: navigate
sec-fetch-site: none
sec-fetch-user: ?1
upgrade-insecure-requests: 1
user-agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/88.0.4324.182 Safari/537.36
"""

combined = {}

for row in headers.split('\n')[1:-1]:
    splitted = row.split(':')
    key = splitted[0]
    val = ''.join(splitted[1:])
    combined[key] = val.strip()


dict_data={'state': [],
           'type' : [],
           'max_price' : [],
           'min_price' : [],
           'address' : [],
           'lat' : [],
           'lng' : [],
           'landArea' : [],
           'builtUp' : [],
           'sizeUnit' : [],
           'level1' : [],
           'level2' : [],
           'level3' : []}

reset_csv_dataset()

for i_type in range(len(lst_type)):
    _type = lst_type[i_type]
    for i_state in range(len(lst_state)):
        _state = lst_state[i_state]
        start_time_State = time.time()
        for i_ptype in range(len(lst_place_type)):
            _ptype = lst_place_type[i_ptype]
            for i_page in tqdm(range(1,max_page+1)):
                try:
                    start_time = time.time()
                    url = f'https://www.iproperty.com.my/{_type}/{_state}/{_ptype}/?l1&page={i_page}'
                    r = requests.get(url, headers=combined)
                    # print(f'\n{url}\nstatus_code: ', r.status_code, r.reason)

                    bs = BeautifulSoup(r.content, 'html5lib')

                    pattern = re.compile('window.__INITIAL_STATE__')
                    script = bs.find("script", text=pattern)

                    data = re.search(r'window\.__INITIAL_STATE__ = ({.*});', script.contents[0]).group(1)
                    # print(data)
                    data = '{"prices"' + re.search(r'"items":\[\{"prices"(.*)}],"isFetching"', data).group(1) + '}]}'

                    data=data.split('{"prices"')
                    data.pop(0)
                    for i in range(len(data)):
                        data[i]='{"prices"'+data[i]

                        data[i] = data[i][:-1]
                        if len(data)== i+1:
                            data[i] = data[i][:-2] + '}'


                    for item in range(len(data)):
                        js_data = json.loads(data[item])
                        print(js_data['prices'])

                        i=attr[0]

                        res_type_price = searchValue(js_data[i], varName='Type', str_regex=r"'type': '(.*?)',")
                        res_min_price = searchValue(js_data[i], varName='min Price', str_regex=r"'min': (.*?),", bln_isNumber=True)
                        res_max_price = searchValue(js_data[i], varName='max Price', str_regex=r"'max':(.*?)}", bln_isNumber=True)

                        i=attr[1]
                        # print(f'{i}= "{str(js_data[i])}"')

                        res_address = searchValue(js_data[i], varName='Formatted Address', str_regex=r"'formattedAddress': '(.*?)',")
                        res_lat = searchValue(js_data[i], varName='Lat', str_regex=r"'lat': (.*?),", bln_isNumber=True)
                        res_lng = searchValue(js_data[i], varName='Lng', str_regex=r"'lng': (.*?),", bln_isNumber=True)

                        i=attr[2]
                        # print(f'{i}= "{str(js_data[i])}"')

                        res_landArea = searchValue(js_data[i], varName='Land Area', str_regex=r"'landArea': '(.*?)',", bln_isNumber=True)
                        res_builtUp = searchValue(js_data[i], varName='Built Up', str_regex=r"'builtUp': '(.*?)',", bln_isNumber=True)
                        res_sizeUnit = searchValue(js_data[i], varName='Size Unit', str_regex=r"'sizeUnit': '(.*?)',")

                        i=attr[3]
                        # print(f'{i}= "{str(js_data[i])}"')

                        res_level1 = searchValue(js_data[i], varName='level1', str_regex=r"'level1': '(.*?)'")
                        res_level2 = searchValue(js_data[i], varName='level2', str_regex=r"'level2': '(.*?)'")
                        res_level3 = searchValue(js_data[i], varName='level3', str_regex=r"'level3': '(.*?)'")

                        # print(f'{item}) type: {res_type_price}, min: {res_min_price}, max: {res_max_price}, formattedAddress: {res_address}, '
                        #       +f'lat: {res_lat}, lng: {res_lng}, landArea: {res_landArea}, builtUp: {res_builtUp}, sizeUnit: {res_sizeUnit}, '
                        #       +f'level1: {res_level1}, level2: {res_level2}, level3: {res_level3}')

                        dict_data['state'] = _state
                        dict_data['type'] = _type
                        dict_data['max_price'] = res_max_price
                        dict_data['min_price'] = res_min_price
                        dict_data['address'] = res_address
                        dict_data['lat'] = res_lat
                        dict_data['lng'] = res_lng
                        dict_data['landArea'] = res_landArea
                        dict_data['builtUp'] = res_builtUp
                        dict_data['sizeUnit'] = res_sizeUnit
                        dict_data['level1'] = res_level1
                        dict_data['level2'] = res_level2
                        dict_data['level3'] = res_level3


                        df = pd.read_csv(ds_name)
                        print(df)
                        df = df.append(dict_data, ignore_index=True)
                        df.to_csv(ds_name, index=False)
                except Exception as e:
                    print(f'\n{url}\nError: Type: {_type}, State: {_state}, ptype: {_ptype}, Page:{i_page}, Error: {e}')
                print(f"{_state} {_type} --- Page  %s seconds ---" % (time.time() - start_time))
        print(f"\nState:{_state} {_type} --- %s seconds ---" % (time.time() - start_time_State))

  0%|                                                   | 0/100 [00:00<?, ?it/s]

[{'type': 'sale', 'currency': 'MYR', 'min': 198000, 'max': 198000}]
Empty DataFrame
Columns: [state, type, max_price, min_price, address, lat, lng, landArea, builtUp, sizeUnit, level1, level2, level3]
Index: []
[{'type': 'sale', 'currency': 'MYR', 'min': 750000, 'max': 750000}]
   state  type  max_price  min_price  \
0  johor  sale     198000     198000   

                                             address       lat         lng  \
0  Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   

   landArea  builtUp     sizeUnit level1       level2  \
0       NaN      403  SQUARE_FEET  Johor  Johor Bahru   

                        level3  
0  Country Garden Central Park  
[{'type': 'sale', 'currency': 'MYR', 'min': 688000, 'max': 688000}]
   state  type  max_price  min_price  \
0  johor  sale     198000     198000   
1  johor  sale     750000     750000   

                                             address       lat         lng  \
0  Persiaran Aliff Harmoni Utama, J

  1%|▍                                          | 1/100 [00:02<04:26,  2.70s/it]

[{'type': 'new', 'currency': 'MYR', 'min': 388000, 'max': 550000}]
    state  type  max_price  min_price  \
0   johor  sale     198000     198000   
1   johor  sale     750000     750000   
2   johor  sale     688000     688000   
3   johor  sale    1096960     588000   
4   johor  sale     400000     400000   
5   johor  sale     750000     750000   
6   johor  sale          0          0   
7   johor  sale    2200000    2200000   
8   johor  sale     150000     150000   
9   johor  sale     935000     935000   
10  johor  sale          0     417000   
11  johor  sale     528000     528000   
12  johor  sale    1250000    1250000   
13  johor  sale     935000     935000   

                                              address       lat         lng  \
0   Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   
1   Jalan Gita, Horizon Hills, Valley West, 79100,...  1.455792  103.629451   
2   Jalan Gita, The Valley West, Horizon Hills, Johor  1.455792  103.629451   
3

[{'type': 'sale', 'currency': 'MYR', 'min': 367000, 'max': 367000}]
    state  type  max_price  min_price  \
0   johor  sale     198000     198000   
1   johor  sale     750000     750000   
2   johor  sale     688000     688000   
3   johor  sale    1096960     588000   
4   johor  sale     400000     400000   
5   johor  sale     750000     750000   
6   johor  sale          0          0   
7   johor  sale    2200000    2200000   
8   johor  sale     150000     150000   
9   johor  sale     935000     935000   
10  johor  sale          0     417000   
11  johor  sale     528000     528000   
12  johor  sale    1250000    1250000   
13  johor  sale     935000     935000   
14  johor  sale     550000     388000   
15  johor  sale    3150000    3150000   
16  johor  sale    1600000    1600000   
17  johor  sale     758000     758000   
18  johor  sale     850000     850000   
19  johor  sale     653000     653000   
20  johor  sale     568000     568000   
21  johor  sale     328000    

...

      state  type  max_price  min_price  \
0     johor  sale     198000     198000   
1     johor  sale     750000     750000   
2     johor  sale     688000     688000   
3     johor  sale    1096960     588000   
4     johor  sale     400000     400000   
...     ...   ...        ...        ...   
2016  johor  sale     270000     270000   
2017  johor  sale     438000     438000   
2018  johor  sale     465000     465000   
2019  johor  sale    1680000    1680000   
2020  johor  sale     460000     460000   

                                                address       lat         lng  \
0     Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   
1     Jalan Gita, Horizon Hills, Valley West, 79100,...  1.455792  103.629451   
2     Jalan Gita, The Valley West, Horizon Hills, Johor  1.455792  103.629451   
3                      Taman Impian Emas, Skudai, Johor  1.570172  103.670159   
4     Jalan Persiaran Danga, Kampung Skudai Kiri, 81...  1.483683  103.714600 

[{'type': 'sale', 'currency': 'MYR', 'min': 398000, 'max': 398000}]
      state  type  max_price  min_price  \
0     johor  sale     198000     198000   
1     johor  sale     750000     750000   
2     johor  sale     688000     688000   
3     johor  sale    1096960     588000   
4     johor  sale     400000     400000   
...     ...   ...        ...        ...   
2022  johor  sale     607000     607000   
2023  johor  sale     680000     680000   
2024  johor  sale     300000     300000   
2025  johor  sale     670000     670000   
2026  johor  sale     420000     420000   

                                                address       lat         lng  \
0     Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   
1     Jalan Gita, Horizon Hills, Valley West, 79100,...  1.455792  103.629451   
2     Jalan Gita, The Valley West, Horizon Hills, Johor  1.455792  103.629451   
3                      Taman Impian Emas, Skudai, Johor  1.570172  103.670159   
4     Jala

[{'type': 'sale', 'currency': 'MYR', 'min': 430000, 'max': 430000}]
      state  type  max_price  min_price  \
0     johor  sale     198000     198000   
1     johor  sale     750000     750000   
2     johor  sale     688000     688000   
3     johor  sale    1096960     588000   
4     johor  sale     400000     400000   
...     ...   ...        ...        ...   
2026  johor  sale     420000     420000   
2027  johor  sale     398000     398000   
2028  johor  sale     635000     635000   
2029  johor  sale     310000     310000   
2030  johor  sale     649000     649000   

                                                address       lat         lng  \
0     Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   
1     Jalan Gita, Horizon Hills, Valley West, 79100,...  1.455792  103.629451   
2     Jalan Gita, The Valley West, Horizon Hills, Johor  1.455792  103.629451   
3                      Taman Impian Emas, Skudai, Johor  1.570172  103.670159   
4     Jala

100%|█████████████████████████████████████████| 100/100 [04:34<00:00,  2.75s/it]

      state  type  max_price  min_price  \
0     johor  sale     198000     198000   
1     johor  sale     750000     750000   
2     johor  sale     688000     688000   
3     johor  sale    1096960     588000   
4     johor  sale     400000     400000   
...     ...   ...        ...        ...   
2028  johor  sale     635000     635000   
2029  johor  sale     310000     310000   
2030  johor  sale     649000     649000   
2031  johor  sale     430000     430000   
2032  johor  sale     280000     280000   

                                                address       lat         lng  \
0     Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   
1     Jalan Gita, Horizon Hills, Valley West, 79100,...  1.455792  103.629451   
2     Jalan Gita, The Valley West, Horizon Hills, Johor  1.455792  103.629451   
3                      Taman Impian Emas, Skudai, Johor  1.570172  103.670159   
4     Jalan Persiaran Danga, Kampung Skudai Kiri, 81...  1.483683  103.714600 

In [4]:
df.head()

state  type max_price min_price  \
0  johor  sale    198000    198000   
1  johor  sale    750000    750000   
2  johor  sale    688000    688000   
3  johor  sale   1096960    588000   
4  johor  sale    400000    400000   

                                             address       lat         lng  \
0  Persiaran Aliff Harmoni Utama, Johor Bahru, 81...  1.511642  103.717577   
1  Jalan Gita, Horizon Hills, Valley West, 79100,...  1.455792  103.629451   
2  Jalan Gita, The Valley West, Horizon Hills, Johor  1.455792  103.629451   
3                   Taman Impian Emas, Skudai, Johor  1.570172  103.670159   
4  Jalan Persiaran Danga, Kampung Skudai Kiri, 81...  1.483683    103.7146   

  landArea    builtUp     sizeUnit level1                      level2  \
0      NaN      403.0  SQUARE_FEET  Johor                 Johor Bahru   
1   1650.0        NaN  SQUARE_FEET  Johor  Iskandar Puteri (Nusajaya)   
2   1400.0     2224.0  SQUARE_FEET  Johor               Horizon Hills   
3      NaN  From 1868          NaN  Johor                      Skudai   
4      NaN       1012  SQUARE_FEET  Johor                      Tampoi   

                                        level3  
0                  Country Garden Central Park  
1                                          NaN  
2                                          NaN  
3  Iconia Garden Residence @ Taman Impian Emas  
4                         Danga View Apartment

In [5]:
# Get the size of scraped data for Johor from 100 pages
df.shape

(2037, 13)

In [6]:
## Convert price from string to int
df['max_price'] = df['max_price'].astype(int)
df['min_price'] = df['min_price'].astype(int)
df.dtypes

state        object
type         object
max_price     int64
min_price     int64
address      object
lat          object
lng          object
landArea     object
builtUp      object
sizeUnit     object
level1       object
level2       object
level3       object
dtype: object

In [7]:
# Checking for missing values
df.isna().sum()

state           0
type            0
max_price       0
min_price       0
address         5
lat           384
lng           384
landArea      876
builtUp        30
sizeUnit       37
level1          0
level2          0
level3       1623
dtype: int64

In [8]:
2037-384

1653

In [9]:
# Double check state - state has to be Johor only
df.state.unique()

array(['johor'], dtype=object)

In [10]:
# Checking max and min for max property price
print(df.max_price.min(),df.max_price.max())

0 15000000


In [11]:
# Checking max and min for min property price
print(df.min_price.min(),df.min_price.max())

0 15000000


### Summary:
- State: Johor
- Maxiumum page scraped in iproperty: 100
- Number of property scraped: 2,037
- Number of property with lat and lon: 1,653